In [ ]:
!pip install transformers torch torchaudio bitsandbytes trl accelerate peft torchcodec datasets[audio] evaluate jiwer tensorboard

In [ ]:
from huggingface_hub import notebook_login

notebook_login()


In [ ]:
import os
import torch
from datasets import load_dataset
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
    HfArgumentParser,
    TrainingArguments,
    pipeline,
    logging,
    WhisperForConditionalGeneration,
    WhisperProcessor,
    WhisperFeatureExtractor,
    WhisperTokenizer,
    Seq2SeqTrainer,
    Seq2SeqTrainingArguments,
)
from peft import LoraConfig, PeftModel
from trl import SFTTrainer
from evaluate import load


In [ ]:
train_ds = load_dataset("MLCommons/peoples_speech", 'microset', split="train")
eval_ds = load_dataset("MLCommons/peoples_speech", 'clean', split="test")

Resolving data files:   0%|          | 0/804 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/804 [00:00<?, ?it/s]

In [ ]:
def prepare_dataset(batch):
    audio = batch["audio"]

    batch["input_features"] = processor.feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]

    batch["labels"] = processor.tokenizer(batch["text"]).input_ids
    return batch


In [ ]:
train_ds = train_ds.map(prepare_dataset)
train_ds[0]

Map:   0%|          | 0/100 [00:00<?, ? examples/s]

{'id': '07282016HFUUforum_SLASH_07-28-2016_HFUUforum_DOT_mp3_00000.flac',
 'audio': <datasets.features._torchcodec.AudioDecoder at 0x7af2836a8140>,
 'duration_ms': 14920,
 'text': "i wanted this to share a few things but i'm going to not share as much as i wanted to share because we are starting late i'd like to get this thing going so we all get home at a decent hour this this election is very important to",
 'input_features': [[0.6303752660751343,
   0.23099517822265625,
   -0.13004827499389648,
   0.27892035245895386,
   0.17800354957580566,
   0.07846927642822266,
   0.2723614573478699,
   0.23907095193862915,
   -0.4905385971069336,
   -0.09561550617218018,
   -0.21035981178283691,
   -0.05820631980895996,
   0.19908004999160767,
   0.08930540084838867,
   0.02327597141265869,
   0.27646273374557495,
   -0.027806997299194336,
   0.026332616806030273,
   0.01602029800415039,
   0.04590481519699097,
   -0.06259393692016602,
   -0.11570394039154053,
   -0.17845964431762695,
   0.0768

In [ ]:
eval_ds = eval_ds.map(prepare_dataset)
eval_ds[0]

Map:   0%|          | 0/50 [00:00<?, ? examples/s]

{'id': '07282016HFUUforum_SLASH_07-28-2016_HFUUforum_DOT_mp3_00100.flac',
 'audio': <datasets.features._torchcodec.AudioDecoder at 0x7af2836a9520>,
 'duration_ms': 14740,
 'text': "in different parties to communicate well and to come up with a viable solution to every problem because conflict is part of life and as we're seeing in most election process is right now that this is where we're bringing people together and trying to organize to develop the vision",
 'input_features': [[0.33764177560806274,
   0.3074175715446472,
   0.1696602702140808,
   0.31461822986602783,
   0.2408795952796936,
   0.2712478041648865,
   0.27968722581863403,
   0.20181405544281006,
   0.19379645586013794,
   0.19186252355575562,
   0.15828055143356323,
   0.212657630443573,
   0.10355228185653687,
   0.198161780834198,
   0.01880824565887451,
   0.08673036098480225,
   0.13933730125427246,
   0.2104467749595642,
   0.2853245139122009,
   0.19001203775405884,
   0.20990079641342163,
   0.36610591411590576,

In [ ]:
metric = load("wer")
def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    label_ids[label_ids == -100] = processor.tokenizer.pad_token_id

    pred_str = processor.tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = processor.tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    wer = 100 * metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}


In [ ]:
#MODEL NAMES
model_name = "openai/whisper-small"
ft_model = "whisper_ft"

#BITSANDBYTES PARAMTERS
use_4bit = True
quant_type = "nf4"
bnb_compute_type = "float16"
nest_quant = False


#QLORA PARAMETERS
rank = 64
alpha = 16
dropout = 0.1
tgt_mod = ["q_proj", "v_proj"]
bias = "none"
task = "SEQ_2_SEQ_LM"


#TRAINING PARAMTERS
output_dir = "./whisper_qlora"
epochs = 1
fp16 = False
bf16 = False
train_batch = 8
eval_batch = 8
grad_steps = 1
max_grad_norm = 0.5
lr = 2e-4
weight_decay = 0.001
warmup_ratio = 0.03
optim = "paged_adamw_32bit"
lr_schedule = "cosine"
group_by_length = True
save_steps = 0
logging_steps = 2
max_steps = 150
report_to = "tensorboard"


#SFT PARAMETERS
device = {"": 0}
max_len = None
packing = False
dataset_text_field = "text"


In [ ]:
processor = WhisperProcessor.from_pretrained(model_name)
processor.tokenizer.language = "english"
processor.tokenizer.task = "transcribe"

preprocessor_config.json: 0.00B [00:00, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

vocab.json: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

merges.txt: 0.00B [00:00, ?B/s]

normalizer.json: 0.00B [00:00, ?B/s]

added_tokens.json: 0.00B [00:00, ?B/s]

special_tokens_map.json: 0.00B [00:00, ?B/s]

In [ ]:
compute_type = getattr(torch, bnb_compute_type)

In [ ]:
bnb_config = BitsAndBytesConfig(
    load_in_4bit = use_4bit,
    bnb_4bit_quant_type = quant_type,
    bnb_4bit_compute_dtype = compute_type,
    bnb_4bit_use_double_quant = nest_quant
)

In [ ]:
model = WhisperForConditionalGeneration.from_pretrained(
    model_name,
    quantization_config = bnb_config,
    device_map = device
)
model.config.use_cache = False
model.config.pretraining_tp = 1

config.json: 0.00B [00:00, ?B/s]

model.safetensors:   0%|          | 0.00/967M [00:00<?, ?B/s]

generation_config.json: 0.00B [00:00, ?B/s]

In [ ]:
peft_config = LoraConfig(
    lora_alpha = alpha,
    lora_dropout = dropout,
    r = rank,
    target_modules = tgt_mod,
    bias = bias,
    task_type = task
)

model = PeftModel(model, peft_config)

In [ ]:
model.generation_config.language = "english"
model.generation_config.task = "transcribe"

model.generation_config.forced_decoder_ids = None


In [ ]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any
    decoder_start_token_id: int

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # Ensure input_features are float16 for compatibility with the quantized model
        batch["input_features"] = batch["input_features"].to(torch.float16)

        label_features = [{"input_ids": feature["labels"]} for feature in features]
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")


        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)
        if (labels[:, 0] == self.decoder_start_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch

In [ ]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(
    processor=processor,
    decoder_start_token_id=model.config.decoder_start_token_id,
)


In [ ]:
training_arguments = Seq2SeqTrainingArguments(
    output_dir = output_dir,
    num_train_epochs = epochs,
    per_device_train_batch_size = train_batch,
    per_device_eval_batch_size=eval_batch,
    gradient_accumulation_steps = grad_steps,
    predict_with_generate=True,
    optim = optim,
    save_steps = save_steps,
    logging_steps = logging_steps,
    learning_rate = lr,
    weight_decay = weight_decay,
    fp16 = fp16,
    bf16 = bf16,
    max_grad_norm = max_grad_norm,
    max_steps = max_steps,
    warmup_ratio = warmup_ratio,
    group_by_length = group_by_length,
    lr_scheduler_type = lr_schedule,
    eval_strategy = "steps",
    eval_steps = 10,
    report_to = report_to,
    metric_for_best_model = "wer",
    push_to_hub = True,
)

In [ ]:
trainer = Seq2SeqTrainer(
    model = model,
    train_dataset = train_ds,
    eval_dataset = eval_ds,
    data_collator = data_collator,
    compute_metrics = compute_metrics,
    processing_class = processor.feature_extractor,
    args = training_arguments,
)

In [ ]:
trainer.train()

TrainOutput(global_step=150, training_loss=0.053841654459635416, metrics={'train_runtime': 751.6279, 'train_samples_per_second': 1.597, 'train_steps_per_second': 0.2, 'total_flos': 3.4538685825024e+17, 'train_loss': 0.053841654459635416, 'epoch': 11.538461538461538})

In [ ]:
kwargs = {
    "dataset_tags": "MLCommons/peoples_speech",
    "dataset": "MLCommons/peoples_speech",
    "language": "en",
    "model_name": "Whisper Small QLoRa",
    "finetuned_from": "openai/whisper-small",
    "tasks": "automatic-speech-recognition",
}


In [ ]:
trainer.push_to_hub(**kwargs)


Processing Files (0 / 0)      : |          |  0.00B /  0.00B            

New Data Upload               : |          |  0.00B /  0.00B            

  ...r_qlora/training_args.bin: 100%|##########| 5.97kB / 5.97kB            

  ...51633.e7720c459a9d.1412.3: 100%|##########| 21.1kB / 21.1kB            

  ...53091.e7720c459a9d.1412.5: 100%|##########| 21.1kB / 21.1kB            

...

  ...51204.e7720c459a9d.1412.1: 100%|##########| 15.7kB / 15.7kB            

  ...53631.e7720c459a9d.1412.6: 100%|##########| 27.9kB / 27.9kB            

  ...51591.e7720c459a9d.1412.2: 100%|##########| 7.45kB / 7.45kB            

  ...adapter_model.safetensors:  89%|########8 | 25.1MB / 28.3MB            

CommitInfo(commit_url='https://huggingface.co/ibraheemaloran/whisper_qlora/commit/ec50096e39197f210055dff6d5a767e6832d034b', commit_message='End of training', commit_description='', oid='ec50096e39197f210055dff6d5a767e6832d034b', pr_url=None, repo_url=RepoUrl('https://huggingface.co/ibraheemaloran/whisper_qlora', endpoint='https://huggingface.co', repo_type='model', repo_id='ibraheemaloran/whisper_qlora'), pr_revision=None, pr_num=None)

In [ ]:
from datasets import load_dataset
import torch
ds = load_dataset("MLCommons/peoples_speech", 'microset', split="train", streaming=True)

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md: 0.00B [00:00, ?B/s]

Resolving data files:   0%|          | 0/804 [00:00<?, ?it/s]

In [ ]:
from transformers import pipeline, WhisperForConditionalGeneration
from peft import PeftModel


base_model = WhisperForConditionalGeneration.from_pretrained(
    "openai/whisper-small",
    quantization_config=bnb_config,
    device_map="auto"
)

model = PeftModel.from_pretrained(
    base_model,
    "ibraheemaloran/whisper_qlora"
)


pipe = pipeline(
    task="automatic-speech-recognition",
    model=model,
    tokenizer=processor.tokenizer,
    feature_extractor=processor.feature_extractor,
)

Device set to use cuda:0


In [ ]:
sample = next(iter(ds))
print(pipe(sample['audio']['array']))


'(ProtocolError('Connection aborted.', RemoteDisconnected('Remote end closed connection without response')), '(Request ID: 5b8a9820-ae6f-4102-b026-5d45992e1e4c)')' thrown while requesting GET https://huggingface.co/datasets/MLCommons/peoples_speech/resolve/f10597c5d3d3a63f8b6827701297c3afdf178272/microset/train-00000-of-00001.parquet
Retrying in 1s [Retry 1/5].


{'text': " I wanted to just share a few things but I'm going to not share as much as I wanted to share because we are starting late. I'd like to get this thing going so we all get home at a decent hour. This this election is very important to"}


In [ ]:
pipe("first_5_minutes.wav", return_timestamps=True)

{'text': " 15 we're going to start our special meeting closed session roll call Council members madrasi here. Oh dear mayor Spencer here three present council members. They saw gonna as you crash Thank you Public comment on closed session items. We have no speaker. Thank you We will now adjourn to closed session to consider 3a conference of legal counsel workers compensation claim Claimant Robert Hunt agency claimed against city of Alameda Thank you everyone I wanted to share we have been in closed session so now we're going to resume our special meeting that started at 615 agenda item for announcement of action taken in closed session if any direction was given to staff now I will adjourn the special that special meeting I will now open the second special city council meeting it is 7.02 p.m. please rise for the Pledge of Allegiance All right, we have a consent calendar, which is routine. However, I wanted to request that we move up. My understanding some people wanted to pull some ite